### PLEASE NOTE

Considering that:
1. In Italian data, Home Confined have never become Recovered
2. A Home Confined case
    * does not need intensive nor sub-intensive therapies
    * is not monitored so won't (likely) never considered as recovered
3. The number of total Recovered is essential to calculate current infected
4. Current infected are calculated as `total_cases - (hospitalized + home_confined)`

from now on
* Home Confined cases (`isolamento_domiciliare` in intalian D.P.C. GitHub repository) will be considered as Recovered.

`Recovered = Recovered + Home_Confined`
* Infected will be consired as 

`infected - home_confined`

Read why [HERE (in intalian)](https://www.maxpierini.it/ncov/italy-ricoveri.html)

***

Plots on this website:
- [Italy (nation)](covid-italy.html)
- [Italy (regions overview)](covid-italy-regions.html)
- [Italy (regions single)](covid-italy-regions-single.html)
- [Italy (regions forecast) **beta test**](covid-italy-regions-forecast.html)
- [Italy (province overview)](covid-italy-province.html)
- [Best 20 countries (overview)](covid-countries-overview.html)
- [Best 20 countries (single)](covid-countries.html)
- [Best 20 countries (forecast) **beta test**](covid-countries-forecast.html)
- [Continents (overview)](covid-continents-overview.html)
- [Continents (single)](covid-continents.html)

Also on this website:
- [Italy & World map](index.php)
- [World real time data and map](covid-arcgis.php)

# ITALY REGIONS FORECAST (beta test)

In [1]:
import json
import requests
import datetime as dt

from IPython.display import Markdown, display, Math

from scipy.optimize import curve_fit
import numpy as np

import plotly.graph_objects as go
import plotly.offline as pyo

pyo.init_notebook_mode()

json_regions = "https://raw.githubusercontent.com/pcm-dpc/COVID-19/master/dati-json/dpc-covid19-ita-regioni.json"
with requests.get(json_regions) as req:
    data = json.loads(req.content.decode('utf-8-sig'))

print("FIRST ENTRY DATE: {}".format(
    data[0]["data"]
    )
)
print("LAST  ENTRY DATE: {}".format(
    data[-1]["data"]
    )
)
period = (
    dt.datetime.strptime(data[-1]["data"], "%Y-%m-%dT%H:%M:%S") -
    dt.datetime.strptime(data[0]["data"], "%Y-%m-%dT%H:%M:%S")
).days

print("COVERAGE: {} days".format(period))
print("CURRENT DATE IS: {}".format(dt.datetime.now().strftime("%Y-%m-%d %H:%M:%S")))

FIRST ENTRY DATE: 2020-02-24T18:00:00
LAST  ENTRY DATE: 2020-04-12T17:00:00
COVERAGE: 47 days
CURRENT DATE IS: 2020-04-12 23:33:59


In [2]:
x = []   # datetime x array
_x = []  # integer x array
yC = {}  # new confirmed cases array
yD = {}  # new deaths array
yR = {}  # new recovered array
yP = {}  # new infected array

TOTyC = {}  # confirmed cases array
TOTyD = {}  # deaths array
TOTyR = {}  # recovered array
TOTyP = {}  # infected array
# TOTyr = {}  # mortality rate
# TOTyk = {}  # recovery rate

for entry in data:

    # x values
    date = dt.datetime.strptime(entry["data"], "%Y-%m-%dT%H:%M:%S")
    if date not in x:
        x.append(date)
        
    region = entry["denominazione_regione"]
    if region not in TOTyC:
        yC.update({region: np.array([])})
        yD.update({region: np.array([])})
        yR.update({region: np.array([])})
        yP.update({region: np.array([])})
        TOTyC.update({region: []})
        TOTyD.update({region: []})
        TOTyR.update({region: []})
        TOTyP.update({region: []})
        # TOTyr.update({region: []})
        # TOTyk.update({region: []})
    # y TOT values
    if len(TOTyC[region]):
        yC[region] = np.append(yC[region], entry["totale_casi"] - TOTyC[region][len(TOTyC[region]) - 1])
        yD[region] = np.append(yD[region], entry["deceduti"] - TOTyD[region][len(TOTyD[region]) - 1])
        yR[region] = np.append(yR[region], (entry["dimessi_guariti"] + entry["isolamento_domiciliare"]) - TOTyR[region][len(TOTyR[region]) - 1])
        yP[region] = np.append(yP[region], (entry["totale_positivi"] - entry["isolamento_domiciliare"]) - TOTyP[region][len(TOTyP[region]) - 1])
    TOTyC[region].append(entry["totale_casi"])
    TOTyD[region].append(entry["deceduti"])
    TOTyR[region].append(entry["dimessi_guariti"] + entry["isolamento_domiciliare"])
    TOTyP[region].append(entry["totale_positivi"] - entry["isolamento_domiciliare"])

_x = [i for i in range(len(x) - 1)]
# forecast x datetime objects
period = 30
xg = [x[-1] + dt.timedelta(days=d + 1) for d in range(period)]
xg = x + xg
# forecast x integer values
_xg = [_x[-1] + d + 1 for d in range(period)]
_xg = _x + _xg

print("len  x: {}".format(len(x)))
print("last  : {}".format(x[-1]))
print("--------------------------")
print("len _x: {}".format(len(_x)))
print("last  : {}".format(_x[-1]))
print("--------------------------")
print("len dy: {}".format(len(yC["Lombardia"])))
print("last  : {}".format(yP["Lombardia"][-1]))
print("--------------------------")
print("len  y: {}".format(len(TOTyP["Lombardia"])))
print("last  : {}".format(TOTyP["Lombardia"][-1]))

len  x: 49
last  : 2020-04-12 17:00:00
--------------------------
len _x: 48
last  : 47
--------------------------
len dy: 48
last  : -55.0
--------------------------
len  y: 49
last  : 13145


In [3]:
def gauss_func(x, a, b, c):
    d = - ((x - b) ** 2)
    return a * np.exp( d / (c ** 2) )

For each region, to perform curve fitting, we will guess initial parameters $p_0$ of gaussian curve

$$ f(t) = a \mathbf{e}^{ -(x - b)^2 / c^2 } $$

as

$$a_0 = \mathbf{P}_{87.5}(y_{>0})$$

$$b_0 = \mathbf{i}_{\mathbf{max}}(y)$$

$$c_0 = \frac{4}{\sqrt{2}} b_0$$

where
$\mathbf{P}_{n}(a_{>0})$ is the $n^{th}$ percentile of array $a$, where $a_{i}>0$

$\mathbf{i}_{\mathbf{max}}(a)$ is the index of maximum element in $a = (a_0, a_1 .. a_n)$

and $y$ is the array of gathered rough data.

In [4]:
for region in yC:
    
    poptC, poptD, poptR = np.array([0, 0, 0]), np.array([0, 0, 0]), np.array([0, 0, 0])
    perrC, perrD, perrR = np.array([0, 0, 0]), np.array([0, 0, 0]), np.array([0, 0, 0])
    
    display(Markdown("## {}".format(region)))
    
    _a0 = np.percentile(yC[region][yC[region] > 0], 87.5)
    a0 = _a0
    b0 = np.where(yC[region] == max(yC[region]))[0][0]
    c0 = (b0 / 4) * np.sqrt(2)
    print("-> CONFIRMED, guessed p0: a0={:.2f}, b0={:.2f}, c0={:.2f}".format(a0, b0, c0))
    if not int(c0):
        c0 = 1
    while int(a0):
        try:
            poptC, pcovC = curve_fit(gauss_func, _x, yC[region], p0=[a0, b0, c0], method="trf")
            perrC = np.sqrt(np.diag(pcovC))
        except RuntimeError as err:
            print("\033[31mERROR: {}\033[0m".format(err))
            print("\033[34m--> force guessed p0\033[0m")
            poptC = np.array([_a0, b0, c0])
            perrC = np.array([_a0 / 2, 1., 1.])
        eSupC = poptC + perrC
        eInfC = poptC - perrC
        a0 -= 1
        if int(poptC[0]):
            break
    if not int(poptC[0]):
        print("\033[1;31mCONFIRMED CURVE FIT ERROR\033[0m")
    else:
        print("\033[32mCONFIRMED CURVE NO ERROR\033[0m")
    display(Math(r"$a={:.2f} \pm {:.2f}$".format(poptC[0], perrC[0])))
    display(Math(r"$b={:.2f} \pm {:.2f}$".format(poptC[1], perrC[1])))
    display(Math(r"$c={:.2f} \pm {:.2f}$".format(abs(poptC[2]), perrC[2])))
        
    _a0 = np.percentile(yD[region][yD[region] > 0], 87.5)
    a0 = _a0
    if not int(a0):
        a0 = 1
    b0 = np.where(yD[region] == max(yD[region]))[0][0]
    c0 = (b0 / 4) * np.sqrt(2)
    print("-> DEATHS, guessed p0: a0={:.2f}, b0={:.2f}, c0={:.2f}".format(a0, b0, c0))
    while int(a0):
        try:
            poptD, pcovD = curve_fit(gauss_func, _x, yD[region], p0=[a0, b0, c0], method="trf")
            perrD = np.sqrt(np.diag(pcovD))
        except RuntimeError as err:
            print("\033[31mERROR: {}\033[0m".format(err))
            print("\033[34m--> force guessed p0\033[0m")
            poptD = np.array([_a0, b0, c0])
            perrD = np.array([_a0 / 2, 1., 1.])
        eSupD = poptD + perrD
        eInfD = poptD - perrD
        a0 -= 1
        if int(poptD[0]):
            break
    if not int(poptD[0]):
        print("\033[1;31mDEATHS CURVE FIT ERROR\033[0m")
    else:
        print("\033[32mDEATHS CURVE NO ERROR\033[0m")
    display(Math(r"$a={:.2f} \pm {:.2f}$".format(poptD[0], perrD[0])))
    display(Math(r"$b={:.2f} \pm {:.2f}$".format(poptD[1], perrD[1])))
    display(Math(r"$c={:.2f} \pm {:.2f}$".format(abs(poptD[2]), perrD[2])))        

    _a0 = np.percentile(yR[region][yR[region] > 0], 87.5)
    a0 = _a0
    if not int(a0):
        a0 = 1
    b0 = np.where(yR[region] == max(yR[region]))[0][0]
    c0 = (b0 / 4) * np.sqrt(2)
    print("-> RECOVERED, guessed p0: a0={:.2f}, b0={:.2f}, c0={:.2f}".format(a0, b0, c0))
    while int(a0):
        try:
            poptR, pcovR = curve_fit(gauss_func, _x, yR[region], p0=[a0, b0, c0], method="trf")
            perrR = np.sqrt(np.diag(pcovR))
        except RuntimeError as err:
            print("\033[31mERROR: {}\033[0m".format(err))
            print("\033[34m--> force guessed p0\033[0m")
            poptR = np.array([_a0, b0, c0])
            perrR = np.array([_a0 / 2, 1., 1.])
        eSupR = poptR + perrR
        eInfR = poptR - perrR
        a0 -= 1
        if int(poptR[0]):
            break
    if not int(poptR[0]):
        print("\033[1;31mRECOVERED CURVE FIT ERROR\033[0m")
    else:
        print("\033[32mRECOVERED CURVE NO ERROR\033[0m")
    display(Math(r"$a={:.2f} \pm {:.2f}$".format(poptR[0], perrR[0])))
    display(Math(r"$b={:.2f} \pm {:.2f}$".format(poptR[1], perrR[1])))
    display(Math(r"$c={:.2f} \pm {:.2f}$".format(abs(poptR[2]), perrR[2])))


    yCg = gauss_func(_xg, *poptC)
    yCgSup = gauss_func(_xg, *eSupC)
    yCgInf = gauss_func(_xg, *eInfC)

    yDg = gauss_func(_xg, *poptD)
    yDgSup = gauss_func(_xg, *eSupD)
    yDgInf = gauss_func(_xg, *eInfD)

    yRg = gauss_func(_xg, *poptR)
    yRgSup = gauss_func(_xg, *eSupR)
    yRgInf = gauss_func(_xg, *eInfR)

    # infected = confirmed - (deaths + recovered)
    yPg = yCg - (yDg + yRg)
    yPgSup = yCgSup - (yDgSup + yRgSup)
    yPgInf = yCgInf - (yDgInf + yRgInf)

    fig = go.Figure()
    # confirmed
    fig.add_trace(go.Scatter(
        x=x[1:], y=yC[region], 
        mode='lines+markers',
        marker_color="blue", marker_size=5, marker_symbol="circle", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="cases", name="new cases/day"
    ))
    if int(poptC[0]):
        fig.add_trace(
            go.Scatter(
                x=xg, y=yCg,
                line_color="blue",
                legendgroup="cases", name="cases gaussian"
            )
        )
        fig.add_trace(go.Scatter(
            x=xg,
            y=yCgInf,
            fill='tonexty',
            fillcolor='rgba(0,0,250,0.25)',
            line_color='rgba(255,255,255,0)',
            legendgroup="cases", showlegend=False,
        ))
        fig.add_trace(go.Scatter(
            x=xg,
            y=yCgSup,
            fill='tonexty',
            fillcolor='rgba(0,0,230,0.25)',
            line_color='rgba(255,255,255,0)',
            legendgroup="cases", showlegend=False,
        ))
    # deaths
    fig.add_trace(go.Scatter(
        x=x[1:], y=yD[region], 
        mode='lines+markers',
        marker_color="red", marker_size=5, marker_symbol="diamond", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="deaths", name="new deaths/day"
    ))
    if int(poptD[0]):
        fig.add_trace(
            go.Scatter(
                x=xg, y=yDg,
                line_color="red",
                legendgroup="deaths", name="deaths gaussian"
            )
        )
        fig.add_trace(go.Scatter(
            x=xg,
            y=yDgInf,
            fill='tonexty',
            fillcolor='rgba(250,0,0,0.25)',
            line_color='rgba(255,255,255,0)',
            legendgroup="deaths", showlegend=False,
        ))
        fig.add_trace(go.Scatter(
            x=xg,
            y=yDgSup,
            fill='tonexty',
            fillcolor='rgba(230,0,0,0.25)',
            line_color='rgba(255,255,255,0)',
            legendgroup="deaths", showlegend=False,
        ))
    # recovered
    fig.add_trace(
        go.Scatter(
        x=x[1:], y=yR[region], 
        mode='lines+markers',
        marker_color="lime", marker_size=5, marker_symbol="square", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="recovered", name="new recovered/day"
    ))
    if int(poptR[0]):
        fig.add_trace(
            go.Scatter(
                x=xg, y=yRg,
                line_color="lime",
                legendgroup="recovered", name="recovered gaussian"
            )
        )
        fig.add_trace(go.Scatter(
            x=xg,
            y=yRgInf,
            fill='tonexty',
            fillcolor='rgba(0,250,0,0.25)',
            line_color='rgba(255,255,255,0)',
            legendgroup="recovered", showlegend=False,
        ))
        fig.add_trace(go.Scatter(
            x=xg,
            y=yRgSup,
            fill='tonexty',
            fillcolor='rgba(0,230,0,0.25)',
            line_color='rgba(255,255,255,0)',
            legendgroup="recovered", showlegend=False,
        ))
    # infected
    fig.add_trace(go.Scatter(
        x=x[1:], y=yP[region], 
        mode='lines+markers',
        marker_color="lightskyblue", marker_size=5, marker_symbol="square",
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="infected", name="new infected/day"
    ))
    fig.add_trace(go.Scatter(
        x=xg, y=yPg,
        line_color="lightskyblue",
        legendgroup="infected", name="infected curve"
    ))
    fig.add_trace(go.Scatter(
        x=xg,
        y=yPgInf,
        fill='tonexty',
        fillcolor='rgba(0,250,250,0.15)',
        line_color='rgba(255,255,255,0)',
        legendgroup="infected", showlegend=False,
    ))
    fig.add_trace(go.Scatter(
        x=xg,
        y=yPgSup,
        fill='tonexty',
        fillcolor='rgba(0,230,230,0.15)',
        line_color='rgba(255,255,255,0)',
        legendgroup="infected", showlegend=False,
    ))
    fig.update_layout(legend_orientation="h",
        showlegend=True, plot_bgcolor='rgba(0,0,0,0)', 
        yaxis={"gridcolor": '#bdbdbd', "zerolinecolor": '#969696'},
        xaxis={"gridcolor": '#bdbdbd'},
        title={"text": "{}, daily increase (gaussian)".format(region), "xanchor": "center", "x": 0.5},
        yaxis_title="new/day",
    )

    pyo.iplot(fig)
    
    # logistic
    # CONFIRMED
    logC = []
    for i, y in enumerate(yCg):
        if not i:
            logC.append(y)
            continue
        logC.append(y + logC[i - 1])
    logCsup = []
    for i, y in enumerate(yCgSup):
        if not i:
            logCsup.append(y)
            continue
        logCsup.append(y + logCsup[i - 1])
    logCinf = []
    for i, y in enumerate(yCgInf):
        if not i:
            logCinf.append(y)
            continue
        logCinf.append(y + logCinf[i - 1])
    # DEATHS
    logD = []
    for i, y in enumerate(yDg):
        if not i:
            logD.append(y)
            continue
        logD.append(y + logD[i - 1])
    logDsup = []
    for i, y in enumerate(yDgSup):
        if not i:
            logDsup.append(y)
            continue
        logDsup.append(y + logDsup[i - 1])
    logDinf = []
    for i, y in enumerate(yDgInf):
        if not i:
            logDinf.append(y)
            continue
        logDinf.append(y + logDinf[i - 1])
    # RECOVERED
    logR = []
    for i, y in enumerate(yRg):
        if not i:
            logR.append(y)
            continue
        logR.append(y + logR[i - 1])
    logRsup = []
    for i, y in enumerate(yRgSup):
        if not i:
            logRsup.append(y)
            continue
        logRsup.append(y + logRsup[i - 1])
    logRinf = []
    for i, y in enumerate(yRgInf):
        if not i:
            logRinf.append(y)
            continue
        logRinf.append(y + logRinf[i - 1])
    # INFECTED
    logP = []
    for i, y in enumerate(yPg):
        if not i:
            logP.append(y)
            continue
        logP.append(y + logP[i - 1])
    logPsup = []
    for i, y in enumerate(yPgSup):
        if not i:
            logPsup.append(y)
            continue
        logPsup.append(y + logPsup[i - 1])
    logPinf = []
    for i, y in enumerate(yPgInf):
        if not i:
            logPinf.append(y)
            continue
        logPinf.append(y + logPinf[i - 1])

    fig = go.Figure()
    # CONFIRMED
    fig.add_trace(
        go.Scatter(
        x=x, y=TOTyC[region],
        mode='lines+markers',
        marker_color="blue", marker_size=5, marker_symbol="circle", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="cases", name="total cases"
    ))
    fig.add_trace(
        go.Scatter(
            x=xg, y=logC,
            line_color="blue",
            legendgroup="cases", name="cases logistic"
        )
    )
    fig.add_trace(go.Scatter(
        x=xg,
        y=logCinf,
        fill='tonexty',
        fillcolor='rgba(0,0,250,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="cases", showlegend=False,
    ))
    fig.add_trace(go.Scatter(
        x=xg,
        y=logCsup,
        fill='tonexty',
        fillcolor='rgba(0,0,230,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="cases", showlegend=False,
    ))
    # DEATHS
    fig.add_trace(go.Scatter(
        x=x, y=TOTyD[region],
        mode='lines+markers',
        marker_color="red", marker_size=5, marker_symbol="diamond", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="deaths", name="total deaths"
    ))
    fig.add_trace(
        go.Scatter(
            x=xg, y=logD,
            line_color="red",
            legendgroup="deaths", name="deaths logistic"
        )
    )
    fig.add_trace(go.Scatter(
        x=xg,
        y=logDinf,
        fill='tonexty',
        fillcolor='rgba(250,0,0,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="deaths", showlegend=False,
    ))
    fig.add_trace(go.Scatter(
        x=xg,
        y=logDsup,
        fill='tonexty',
        fillcolor='rgba(230,0,0,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="deaths", showlegend=False,
    ))
    # RECOVERED
    fig.add_trace(go.Scatter(
        x=x, y=TOTyR[region],
        mode='lines+markers',
        marker_color="lime", marker_size=5, marker_symbol="square", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="recovered", name="total recovered"
    ))
    fig.add_trace(
        go.Scatter(
            x=xg, y=logR,
            line_color="lime",
            legendgroup="recovered", name="recovered logistic"
        )
    )
    fig.add_trace(go.Scatter(
        x=xg,
        y=logRinf,
        fill='tonexty',
        fillcolor='rgba(0,250,0,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="recovered", showlegend=False,
    ))
    fig.add_trace(go.Scatter(
        x=xg,
        y=logRsup,
        fill='tonexty',
        fillcolor='rgba(0,230,0,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="recovered", showlegend=False,
    ))
    # INFECTED
    fig.add_trace(go.Scatter(
        x=x, y=TOTyP[region],
        mode='lines+markers',
        marker_color="lightskyblue", marker_size=5, marker_symbol="x", marker_line_width=1,
        line={"dash": "dot"}, line_shape='spline',
        legendgroup="infected", name="current infected"
    ))
    fig.add_trace(
        go.Scatter(
            x=xg, y=logP,
            line_color="lightskyblue",
            legendgroup="infected", name="infected curve"
        )
    )
    fig.add_trace(go.Scatter(
        x=xg,
        y=logPinf,
        fill='tonexty',
        fillcolor='rgba(0,250,250,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="infected", showlegend=False,
    ))
    fig.add_trace(go.Scatter(
        x=xg,
        y=logPsup,
        fill='tonexty',
        fillcolor='rgba(0,230,230,0.25)',
        line_color='rgba(255,255,255,0)',
        legendgroup="infected", showlegend=False,
    ))
    # update layout
    fig.update_layout(legend_orientation="h",
        showlegend=True, plot_bgcolor='rgba(0,0,0,0)', 
        yaxis={"gridcolor": '#bdbdbd', "zerolinecolor": '#969696'},
        xaxis={"gridcolor": '#bdbdbd'},
        title={"text": "{}, total amount (logistic)".format(region), "xanchor": "center", "x": 0.5},
        yaxis_title="number",
    )
    pyo.iplot(fig)
        
    display(Markdown("---"))

## Abruzzo

-> CONFIRMED, guessed p0: a0=100.25, b0=33.00, c0=11.67
CONFIRMED CURVE NO ERROR


<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

...

-> RECOVERED, guessed p0: a0=438.00, b0=44.00, c0=15.56
RECOVERED CURVE NO ERROR


<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

---